# Connection to MYSQL through Python

So the libraries work correctly it is important to get Python 3.7 or below, also the "sqlalchemy" library is not found in Anaconda or Colab therefore is recommended to run this code through cmd.

Some other important tools:

* Xampp
* MySQL
* Qgis

_The used data for this project can be found in the following link:_ [https://drive.google.com/drive/folders/1Tn8qlEOmWxUU51idEdgRfWRM5k35JtA_?usp=sharing]

In [1]:
#Libraries for the MySQL connection
import csv
import pymysql
import pandas as pd
from sqlalchemy import create_engine, types
import mysql.connector 

#libraries to use the Mapper algorithm
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import random
import sklearn
import datetime as dt 

from sklearn.preprocessing import LabelEncoder 
#Encode target labels with value between 0 and n_classes-1.
from sklearn.preprocessing import StandardScaler 
#Standardize features by removing the mean and scaling to unit variance.

from sklearn.decomposition import PCA 
#Principal component analysis (PCA).
#Linear dimensionality reduction using Singular Value Decomposition of the data to project it to a lower dimensional space. 
#The input data is centered but not scaled for each feature before applying the SVD.

from sklearn.manifold import TSNE
#t-distributed Stochastic Neighbor Embedding. It's a tool to visualize high-dimensional data.

from sklearn import datasets
import umap.umap_ as umap
#Uniform Manifold Approximation and Projection (UMAP) is a dimension reduction technique that can be used for visualisation
#similarly to t-SNE, but also for general non-linear dimension reduction. 

import kmapper as km
from kmapper import jupyter 
#Creates custom CSS full-size Jupyter screen.

from sklearn import preprocessing
#Provides several common utility functions and transformer classes to change raw feature vectors into a representation
#that is more suitable for the downstream estimators.

import warnings
warnings.filterwarnings('ignore')

In [2]:
#Testing connection
mydb = mysql.connector.connect( 
  host = "localhost", 
  user = "root", 
  password = "", 
  database = "prueba"
)  
  
mycursor = mydb.cursor() 

INSERTING DATA TO THE DATABASE

* *ITER*

In [3]:
engine = create_engine('mysql://root:@localhost/prueba')
df = pd.read_csv("iter_13_cpv2010.csv",sep=',',quotechar='\'',encoding='utf8') 
df.to_sql('iter',con=engine,index=False,if_exists='append')

* *DRENAJE*

In [9]:
engine = create_engine('mysql://root:@localhost/prueba')
df = pd.read_csv("hidalgo_drenaje.csv",sep=',',quotechar='\'',encoding='utf8') 
df.to_sql('drenaje',con=engine,index=False,if_exists='append')

* *UBICACIÓN*

In [11]:
engine = create_engine('mysql://root:@localhost/prueba')
df = pd.read_csv("ubicacion.csv",sep=',',quotechar='\'',encoding='utf8') 
df.to_sql('ubicación',con=engine,index=False,if_exists='append')

* *COVID*

In [40]:
engine = create_engine('mysql://root:@localhost/prueba')
df = pd.read_csv("FinalDatasetCovid.csv",sep=',',quotechar='\'',encoding='utf8') 
df.to_sql('covid',con=engine,index=False,if_exists='append')

* *DRENAJE SEGUNDA*

In [7]:
engine = create_engine('mysql://root:@localhost/prueba')
df = pd.read_csv("DrenajeN.csv",sep=',',quotechar='\'',encoding='utf8') 
df.to_sql('DrenajeN',con=engine,index=False,if_exists='append')

* SELECTING DATA

In [3]:
#Code to check whether the query is executed successfully or not
''' mycursor.execute("SELECT latitud,longitud FROM covid")
myresult = mycursor.fetchall()
for x in myresult:
  print(x)  '''

# Read the SQL query results using pandas
queryframe = pd.read_sql("""
            SELECT *FROM covid
            """, con = mydb)

# Return the first five rows
queryframe.head()



Unnamed: 0 ID_REGISTRO  Nom_Ent           Nom_Mun  \
0           0      0cde25  Hidalgo  Huasca de Ocampo   
1           1      0cde25  Hidalgo  Huasca de Ocampo   
2           2      0cde25  Hidalgo  Huasca de Ocampo   
3           3      0cde25  Hidalgo  Huasca de Ocampo   
4           4      0cde25  Hidalgo  Huasca de Ocampo   

                       Nom_Loc  Lat_Decimal  Lon_Decimal  Altitud  \
0             Huasca de Ocampo    20.203611   -98.577615     2098   
1  Aguacatitla (El Campamento)    20.248261   -98.549398     2029   
2                     Bermúdez    20.191681   -98.594501     2227   
3          San José Cacaloapan    20.199611   -98.484039     2126   
4                    La Cañada    20.273458   -98.586490     2026   

  FECHA_ACTUALIZACION FECHA_INGRESO FECHA_SINTOMAS  INTUBADO  UCI  
0          09/11/2020    25/03/2020     18/03/2020         2    2  
1          09/11/2020    25/03/2020     18/03/2020         2    2  
2          09/11/2020    25/03/2020     18/03/2020         2    2  
3          09/11/2020    25/03/2020     18/03/2020         2    2  
4          09/11/2020    25/03/2020     18/03/2020         2    2

In [4]:
#Making groups 
categorical_columns = [ 'INTUBADO', 'UCI']
numerical_columns = ['Lat_Decimal', 'Lon_Decimal']
date_columns = ['FECHA_ACTUALIZACION', 'FECHA_INGRESO']

#Select columns
df = queryframe[~queryframe['Nom_Loc'].isna()][categorical_columns + numerical_columns + date_columns ]

#Vectorize ads
labelencoder = LabelEncoder()
df['encoded_start_date'] = labelencoder.fit_transform(df['FECHA_INGRESO'])
df = df.drop(['FECHA_ACTUALIZACION', 'FECHA_INGRESO'], axis = 1)
df = pd.get_dummies(df, columns = categorical_columns)

#Drop null data
df = df.dropna()
index = df.index

#Scale data
df = StandardScaler().fit_transform(df.values)
df.shape

(989572, 11)

* VISUALIZING THE DATAFRAME

In [ ]:
#Creating a function to visualize the data

def visualize_scatter(data_2d, column, figsize=(20,20)):

    plt.figure(figsize=figsize)
    
    # Set labels
    labels = queryframe.loc[index][column]
    label_to_id_dict = {v:i for i,v in enumerate(np.unique(labels))}
    id_to_label_dict = {v: k for k, v in label_to_id_dict.items()}
    label_ids = np.array([label_to_id_dict[x] for x in labels])

    nb_classes = len(np.unique(label_ids))
    
    for label_id in np.unique(label_ids):
        plt.scatter(data_2d[np.where(label_ids == label_id), 0],
                    data_2d[np.where(label_ids == label_id), 1],
                    marker='o',
                    color= plt.cm.gist_ncar(label_id / float(nb_classes)),
                    linewidth='1',
                    alpha=0.4,
                    label=id_to_label_dict[label_id])
        ax = plt.gca()
    plt.legend(loc='right')
    
    ax.set_facecolor('xkcd:black')

In [6]:
#Creating objects of each one of the functions to visualize the data 
tsne = TSNE(n_components=2, perplexity=40.0)
tsne_result = tsne.fit_transform(df)

reducer = umap.UMAP(n_neighbors = 40)
embedding = reducer.fit_transform(df)

pca = PCA(n_components=2)
principalComponents = pca.fit_transform(df)

MemoryError: could not allocate 524288000 bytes

Exception ignored in: 'sklearn.neighbors._quad_tree._QuadTree._insert_point_in_new_child'
Traceback (most recent call last):
  File "sklearn\neighbors\_quad_tree.pyx", line 586, in sklearn.neighbors._quad_tree._QuadTree._resize
  File "sklearn\neighbors\_quad_tree.pyx", line 606, in sklearn.neighbors._quad_tree._QuadTree._resize_c
  File "sklearn\tree\_utils.pyx", line 41, in sklearn.tree._utils.safe_realloc
MemoryError: could not allocate 524288000 bytes


MemoryError: could not allocate 524288000 bytes

Exception ignored in: 'sklearn.neighbors._quad_tree._QuadTree._insert_point_in_new_child'
Traceback (most recent call last):
  File "sklearn\neighbors\_quad_tree.pyx", line 586, in sklearn.neighbors._quad_tree._QuadTree._resize
  File "sklearn\neighbors\_quad_tree.pyx", line 606, in sklearn.neighbors._quad_tree._QuadTree._resize_c
  File "sklearn\tree\_utils.pyx", line 41, in sklearn.tree._utils.safe_realloc
MemoryError: could not allocate 524288000 bytes


MemoryError: could not allocate 524288000 bytes

...

MemoryError: could not allocate 524288000 bytes

Exception ignored in: 'sklearn.neighbors._quad_tree._QuadTree._insert_point_in_new_child'
Traceback (most recent call last):
  File "sklearn\neighbors\_quad_tree.pyx", line 586, in sklearn.neighbors._quad_tree._QuadTree._resize
  File "sklearn\neighbors\_quad_tree.pyx", line 606, in sklearn.neighbors._quad_tree._QuadTree._resize_c
  File "sklearn\tree\_utils.pyx", line 41, in sklearn.tree._utils.safe_realloc
MemoryError: could not allocate 524288000 bytes


MemoryError: could not allocate 524288000 bytes

Exception ignored in: 'sklearn.neighbors._quad_tree._QuadTree._insert_point_in_new_child'
Traceback (most recent call last):
  File "sklearn\neighbors\_quad_tree.pyx", line 586, in sklearn.neighbors._quad_tree._QuadTree._resize
  File "sklearn\neighbors\_quad_tree.pyx", line 606, in sklearn.neighbors._quad_tree._QuadTree._resize_c
  File "sklearn\tree\_utils.pyx", line 41, in sklearn.tree._utils.safe_realloc
MemoryError: could not allocate 524288000 bytes


MemoryError: Unable to allocate 1.09 GiB for an array with shape (146069654,) and data type int64

In [ ]:
#Showing the results from the PCA function
visualize_scatter(principalComponents, 'nom_loc')